In [3]:
-- http://www.haskellforall.com/2012/06/you-could-have-invented-free-monads.html

{-| 
data Toy b
    = Output b (Toy b)
    | Bell (Toy b)
    | Done
-}

data Toy b next =
    Output b next
  | Bell next
  | Done
  
-- A simple program
-- output 'A'
-- done
:t (Output 'A' Done)

-- bell
-- output 'A'
-- done
:t (Bell (Output 'A' Done))

(Output 'A' Done) :: forall b next. Toy Char (Toy b next)

(Bell (Output 'A' Done)) :: forall b1 b2 next. Toy b1 (Toy Char (Toy b2 next))

In [9]:
data Fix f = Fix (f (Fix f))

:t (Fix (Output 'A' (Fix Done)))

:t (Fix (Bell (Fix (Output 'A' (Fix Done)))))

-- cosine x = x
-- x = 0.7...

-- f x = x

(Fix (Output 'A' (Fix Done))) :: Fix (Toy Char)

(Fix (Bell (Fix (Output 'A' (Fix Done))))) :: Fix (Toy Char)

In [10]:
{-# LANGUAGE FlexibleContexts #-}

-- https://hackage.haskell.org/package/base-4.12.0.0/docs/Control-Monad-Fix.html
import Control.Monad.Fix

-- fix :: (a -> a) -> a
-- fix f = let {x = f x} in x

let fac n = if n <= 1 then 1 else n * fac (n-1) in fac 5

fix (\rec n -> if n <= 1 then 1 else n * rec (n-1)) 5

-- fix fact' 5
fact' rec n = if n == 0 then 1 else n * rec (n-1)

:t fact'

-- f = fact' f
--   = \n -> if n == 0 then 1 else n * f (n-1)

{-|
  fix fact'
= fact' (fix fact')
= (\rec n -> if n == 0 then 1 else n * rec (n-1)) (fix fact')
= \n -> if n == 0 then 1 else n * fix fact' (n-1)
= \n -> if n == 0 then 1 else n * fact' (fix fact') (n-1)
= \n -> if n == 0 then 1
        else n * (\rec n' -> if n' == 0 then 1 else n' * rec (n'-1)) (fix fact') (n-1)
= \n -> if n == 0 then 1
        else n * (if n-1 == 0 then 1 else (n-1) * fix fact' (n-2))
= \n -> if n == 0 then 1
        else n * (if n-1 == 0 then 1
                  else (n-1) * (if n-2 == 0 then 1
                                else (n-2) * fix fact' (n-3)))
= ...
-}

fix fact' 5

120

120

fact' :: forall p. (Eq p, Num p) => (p -> p) -> p -> p

120

In [5]:
data FixE f e = Fix (f (FixE f e)) | Throw e

-- data Free f r = Free (f (Free f r)) | Pure r

catch :: (Functor f) => FixE f e1 -> (e1 -> FixE f e2) -> FixE f e2
catch (Fix x) f = Fix (fmap (flip catch f) x)
catch (Throw e) f = f e

instance Functor (Toy b) where
    fmap f (Output x next) = Output x (f next)
    fmap f (Bell     next) = Bell     (f next)
    fmap f  Done           = Done
    
data IncompleteException = IncompleteException

-- output 'A'
-- throw IncompleteException
-- output 'B'
subroutine = Fix (Output 'A' (Throw IncompleteException)) :: FixE (Toy Char) IncompleteException

-- try {subroutine}
-- catch (IncompleteException) {
--     bell
--     done
-- }
program = subroutine `catch` (\_ -> Fix (Bell (Fix Done))) :: FixE (Toy Char) e

Line 4: Use section
Found:
(flip catch f)
Why not:
(`catch` f)

In [6]:
import Control.Monad.Free

{-|
data Free f r = Free (f (Free f r)) | Pure r

instance (Functor f) => Monad (Free f) where
    return = Pure
    (Free x) >>= f = Free (fmap (>>= f) x)
    (Pure r) >>= f = f r
-}

{-|
(>>=) :: forall a b. m a -> (a -> m b) -> m b
catch :: (Functor f) => FixE f e1 -> (e1 -> FixE f e2) -> FixE f e2

FixE f --- m
e1     --- a
e2     --- b

catch -- >>=
Throw -- Pure
-}

{-|
output :: a -> Free (Toy a) ()
output x = Free (Output x (Pure ()))

bell :: Free (Toy a) ()
bell = Free (Bell (Pure ()))

done :: Free (Toy a) r
done = Free Done

liftF :: (Functor f) => f r -> Free f r
liftF command = Free (fmap Pure command)
-}

-- There is some Functor f => Free f is a monad

-- Toy b is a Functor, Free (Toy b) is a monad

output x = liftF (Output x ())
bell     = liftF (Bell     ())
done     = liftF  Done

:t output
:t bell
:t done

subroutine :: Free (Toy Char) ()
subroutine = output 'A'

program :: Free (Toy Char) r
program = do
    bell
    subroutine
    bell
    done

output :: forall b (m :: * -> *). MonadFree (Toy b) m => b -> m ()

bell :: forall b (m :: * -> *). MonadFree (Toy b) m => m ()

done :: forall b (m :: * -> *) a. MonadFree (Toy b) m => m a

In [7]:
showProgram :: (Show a, Show r) => Free (Toy a) r -> String
showProgram (Free (Output a x)) =
    "output " ++ show a ++ "\n" ++ showProgram x
showProgram (Free (Bell x)) =
    "bell\n" ++ showProgram x
showProgram (Free Done) =
    "done\n"
showProgram (Pure r) =
    "return " ++ show r ++ "\n"
    
putStr (showProgram program)

bell
output 'A'
bell
done

In [25]:
pretty :: (Show a, Show r) => Free (Toy a) r -> IO ()
pretty = putStr . showProgram

pretty (output 'A')

pretty (return 'A' >>= output)

pretty (output 'A' >>= return)

pretty ((output 'A' >> done) >> output 'C')

pretty (output 'A' >> (done >> output 'C'))

Line 6: Monad law, left identity
Found:
return 'A' >>= output
Why not:
output 'A'Line 8: Monad law, right identity
Found:
output 'A' >>= return
Why not:
output 'A'

output 'A'
return ()

output 'A'
return ()

output 'A'
return ()

output 'A'
done

output 'A'
done

In [43]:
-- data Free f r = Free (f (Free f r)) | Pure r

data List a   = Cons  a (List a  )  | Nil

type List' a = Free ((,) a) ()

{-|
List' a
= Free ((,) a) ()
= Free (a, List' a)) | Pure ()
= Free a (List' a) | Pure ()
-}

In [9]:
{-|

data Request =
    Look Direction
  | ReadLine
  | Fire Direction
  | WriteLine String
  
data Response =
    Image Picture     -- Response for Look
  | ChatLine String   -- Response for Read
  | Succeeded Bool    -- Response for Write
  
data Interaction next =
    Look Direction (Image -> next)
  | Fire Direction next
  | ReadLine (String -> next)
  | WriteLine String (Bool -> next)
  
instance Functor Interaction where
    fmap f (Look dir g) = Look dir (f . g)
    fmap f (Fire dir x) = Fire dir (f x)
    fmap f (ReadLine g) = ReadLine (f . g)
    fmap f (WriteLine s g) = WriteLine s (f . g)
    
interpret :: Program r -> Game r
interpret prog = case prog of
    Free (Look dir g) -> do
        img <- collectImage dir
        interpret (g img)
    Free (Fire dir next) -> do
        sendBullet dir
        interpret next
    Free (ReadLine g) -> do
        str <- getChatLine
        interpret (g str)
    Free (WriteLine s g) ->
        putChatLine s
        interpret (g True)
    Pure r -> return r
-}

In [45]:
-- Taken from some gist on the internet
import Control.Monad.Free
import Control.Monad.Trans
import System.Directory

-- | Define our Free Monad DSL
data FileF r =
  Write String String r
  | Delete String r
  | Copy String String r
  | Move String String r
  | Read (String -> r)
  | Log String r
  deriving (Functor)

-- | Smart constructors
write :: String -> String -> Free FileF ()
write path txt = liftF $ Write path txt ()

delete :: String -> Free FileF ()
delete path = liftF $ Delete path ()

copy :: String -> String -> Free FileF ()
copy from to = liftF $ Copy from to ()

move :: String -> String -> Free FileF ()
move from to = liftF $ Move from to ()

readLine :: Free FileF String
readLine = liftF $ Read id

logMsg :: String -> Free FileF ()
logMsg msg = liftF $ Log msg ()

-- | We can transform our data structure before execution
optimizeMove :: Free FileF a -> Free FileF a
optimizeMove (Pure a) = Pure a
optimizeMove (Free (Copy from to (Free (Delete f r)))) | f == from = Free $ Move from to (optimizeMove r)
optimizeMove (Free f) = Free (fmap optimizeMove f)


-- | Log each action we take
addLogging :: Free FileF a -> Free FileF a
addLogging (Pure a) = Pure a
addLogging (Free f@(Write path txt _)) = Free (Log ("Writing " ++ txt ++ " to " ++ path) (Free $ fmap addLogging f))
addLogging (Free f@(Delete path _)) = Free (Log ("Deleting " ++ path) (Free $ fmap addLogging f))
addLogging (Free f@(Copy from to _)) = Free (Log ("Copying " ++ from ++ " to " ++ to) (Free $ fmap addLogging f))
addLogging (Free f@(Move from to _)) = Free (Log ("Moving " ++ from ++ " to " ++ to) (Free $ fmap addLogging f))
addLogging (Free (Read f)) = Free (Read (\txt -> Free (Log ("Read " ++ txt ++ " from console") (addLogging (f txt)))))
addLogging (Free f) = Free (fmap addLogging f)


-- | We can run our FileF as IO
interpToIO :: Free FileF () -> IO ()
interpToIO (Pure ()) = return ()
interpToIO (Free (Write path txt r)) = writeFile path txt >> interpToIO r
interpToIO (Free (Delete path r)) = removeFile path >> interpToIO r
interpToIO (Free (Copy from to r)) = copyFile from to >> interpToIO r
interpToIO (Free (Move from to r)) = renameFile from to >> interpToIO r
interpToIO (Free (Read f)) = getLine >>= interpToIO . f
interpToIO (Free (Log msg r)) = putStrLn msg >> interpToIO r

-- | Here's a program
operations :: Free FileF ()
operations = do
  write "helloworld.txt" "Hello, World!"
  logMsg "Enter new filename"
  newFilename <- readLine
  if newFilename == "quit"
     then logMsg "See ya later"
     else copy "helloworld.txt" newFilename >> delete "helloworld.txt"


-- Note how we can now perform arbitrary optimizations over our calculations
-- We can compose our optimizations in any order to get the effects we want;
-- Note how (optimizeMove . addLogging) is different from  (addLogging . optimizeMove)
loggedOptimized :: IO ()
loggedOptimized = interpToIO . optimizeMove .  addLogging $ operations
-- > λ> loggedOptimized
-- > Writing Hello, World! to helloworld.txt
-- > Enter new filename
-- > NEW
-- > Read NEW from console
-- > Copying helloworld.txt to NEW
-- > Deleting helloworld.txt

optimizedLogged :: IO ()
optimizedLogged = interpToIO . addLogging . optimizeMove $ operations
-- > λ> optimizedLogged
-- > Writing Hello, World! to helloworld.txt
-- > Enter new filename
-- > NEW
-- > Read NEW from console
-- > Moving helloworld.txt to NEW